In [ ]:
from pathlib import Path

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from misc import model_config

In [2]:
main_model_config = (
    model_config.query("main")
    .drop(columns="main")
    .rename(columns={k: f"model_{k}" for k in model_config.columns})
)

new_name = {
    "powermoe": "PowerMoE",
    "llamamoe": "LLaMA-MoE-v1",
    "olmoe": "OLMoE",
    "switch": "SwitchTransformers",
    "llamamoe2": "LLaMA-MoE-v2",
    "jetmoe": "JetMoE",
    "openmoe": "OpenMoE",
    "minicpm": "MiniCPM-MoE",
    "qwen": "Qwen1.5-MoE",
    "deepseek2": "DeepSeek-V2-Lite",
    "deepseek": "DeepSeekMoE",
    "xverse": "XVERSE-MoE",
    "qwen3": "Qwen3",
    "yuan": "Yuan2.0",
    "phi": "Phi-3.5-MoE",
    "grin": "GRIN-MoE",
    "mixtral": "Mixtral-8x7B",
    "jamba": "Jamba-Mini",
    "nllb": "NLLB-MoE",
    "qwen2": "Qwen2",
}

model_colors = {
    key: px.colors.qualitative.Dark24[i] for i, key in enumerate(main_model_config.index.values)
}

seg_lens = (4, 16, 64, 256)
seg_len_colors = {key: px.colors.qualitative.Plotly[i] for i, key in enumerate(seg_lens)}
main_model_config

model_name model_abbr model_type  \
key                                                            
powermoe                   PowerMoE-3B         PW     causal   
llamamoe             LLaMA-MoE-v1-3.5B        LL1     causal   
olmoe                 OLMoE-1B-7B-0125         OL     causal   
switch     SwitchTransformers-Base-128         ST    seq2seq   
llamamoe2            LLaMA-MoE-v2-3.8B        LL2     causal   
jetmoe                       JetMoE-8B         JT     causal   
openmoe                     OpenMoE-8B         OP     causal   
minicpm               MiniCPM-MoE-8x2B         MC     causal   
qwen                 Qwen1.5-MoE-A2.7B        QW1     causal   
deepseek2             DeepSeek-V2-Lite        DS2     causal   
deepseek                   DeepSeekMoE        DS1     causal   
xverse                XVERSE-MoE-A4.2B         XV     causal   
qwen3                    Qwen3-30B-A3B        QW3     causal   
yuan                       Yuan2.0-M32         Y2     causal   
phi                        Phi-3.5-MoE         PH     causal   
grin                          GRIN-MoE         GR     causal   
mixtral              Mixtral-8x7B-v0.1         MX     causal   
jamba                   Jamba-Mini-1.6         JB     causal   
nllb                      NLLB-MoE-54B         NL    seq2seq   
qwen2                   Qwen2-57B-A14B        QW2     causal   

           model_num_params  model_num_layers  model_num_experts  model_top_k  \
key                                                                             
powermoe               3.30                32                 40            8   
llamamoe               6.74                32                 16            4   
olmoe                  6.92                16                 64            8   
switch                 7.42                24                128            1   
llamamoe2              8.03                32                  8            2   
jetmoe                 8.52                24                  8            2   
openmoe               11.86                24                 32            2   
minicpm               13.87                40                  8            2   
qwen                  14.32                24                 60            4   
deepseek2             15.71                27                 64            6   
deepseek              16.38                28                 64            6   
xverse                25.78                28                 64            6   
qwen3                 30.53                48                128            8   
yuan                  39.94                24                 32            2   
phi                   41.87                32                 16            2   
grin                  41.87                32                 16            2   
mixtral               46.70                32                  8            2   
jamba                 51.57                32                 16            2   
nllb                  54.50                48                128            2   
qwen2                 57.41                28                 64            8   

                  model_attn  
key                           
powermoe   flash_attention_2  
llamamoe               eager  
olmoe      flash_attention_2  
switch                 eager  
llamamoe2  flash_attention_2  
jetmoe     flash_attention_2  
openmoe                eager  
minicpm    flash_attention_2  
qwen       flash_attention_2  
deepseek2  flash_attention_2  
deepseek   flash_attention_2  
xverse     flash_attention_2  
qwen3      flash_attention_2  
yuan       flash_attention_2  
phi        flash_attention_2  
grin       flash_attention_2  
mixtral    flash_attention_2  
jamba      flash_attention_2  
nllb                   eager  
qwen2      flash_attention_2

In [3]:
def make_abbr(df):
    return (
        f"{df['model_abbr']}{'d' if df['is_decoder'] else 'e'}"
        if df["model_type"] == "seq2seq"
        else df["model_abbr"]
    )

In [ ]:
root_dir = Path("../output/srp_mpq")

dfs = {
    p.stem: pd.merge(pd.read_parquet(p), main_model_config, left_on="model", right_index=True)
    for p in root_dir.glob("*.parquet")
}

for df in dfs.values():
    df["model"] = df["model"].astype(model_config.index.dtype)

sorted_model_keys = (
    dfs["mg"].query("is_decoder and seg_len == 16").sort_values("best_f1", ascending=False)["model"]
)

dfs["mg"].pivot(index=["model", "is_decoder"], columns="seg_len", values=["best_f1", "best_m"])

best_f1                                  best_m  \
seg_len                    4         16        64        256       4     
model     is_decoder                                                     
powermoe  True        0.673095  0.551720  0.505882  0.485872  1.103515   
llamamoe  True        0.557779  0.452880  0.416099  0.406180  1.029198   
olmoe     True        0.646949  0.509072  0.455343  0.426438  0.997344   
switch    False       0.416367  0.193265  0.123377  0.099904  3.803456   
          True        0.418338  0.192715  0.117753       NaN  3.780828   
llamamoe2 True        0.831850  0.781586  0.764461  0.754810  1.120930   
jetmoe    True        0.602158  0.474540  0.427762  0.410949  1.093253   
openmoe   True        0.455252  0.287725  0.217618  0.187988  3.393169   
minicpm   True        0.625336  0.488538  0.437157  0.417272  1.105926   
qwen      True        0.472319  0.307060  0.225031  0.187072  3.234429   
deepseek2 True        0.532088  0.379159  0.306759  0.269236  0.842495   
deepseek  True        0.522833  0.369363  0.295573  0.257484  0.828959   
xverse    True        0.536069  0.385817  0.311247  0.274691  0.822890   
qwen3     True        0.672163  0.541430  0.478911  0.438075  0.993253   
yuan      True        0.711998  0.634819  0.611333  0.598330  0.968449   
phi       True        0.651531  0.519771  0.466027  0.437805  1.015194   
grin      True        0.637753  0.503854  0.450368  0.421200  0.998881   
mixtral   True        0.625494  0.493599  0.445111  0.424732  1.115575   
jamba     True        0.530930  0.380786  0.311767  0.279440  0.872411   
nllb      False       0.444048  0.252397  0.195115  0.165326  3.504017   
          True        0.456684  0.313525  0.261670  0.219095  3.379399   
qwen2     True        0.502406  0.367437  0.303384  0.275186  0.818744   

                                                    
seg_len                    16        64        256  
model     is_decoder                                
powermoe  True        1.392749  1.488992  1.579756  
llamamoe  True        2.392017  2.923047  3.521086  
olmoe     True        1.056418  1.205091  1.187848  
switch    False       2.009145  2.649861  1.913562  
          True        2.059083  2.665879       NaN  
llamamoe2 True        1.034675  1.058977  1.062069  
jetmoe    True        2.259037  2.687439  3.154335  
openmoe   True        1.588945  2.635040  2.177667  
minicpm   True        2.186703  2.578770  2.916163  
qwen      True        1.842482  2.105532  2.889928  
deepseek2 True        1.283745  1.993245  2.015406  
deepseek  True        2.291513  1.933054  2.234304  
xverse    True        1.237651  1.899895  1.800314  
qwen3     True        1.065951  1.094106  1.117714  
yuan      True        0.884136  0.923747  0.914294  
phi       True        1.141190  1.354095  1.301607  
grin      True        1.107831  1.305612  1.362187  
mixtral   True        2.175447  2.287126  2.751702  
jamba     True        1.461244  2.580545  2.797719  
nllb      False       1.171920  1.649572  1.759518  
          True        1.417110  1.340723  1.454345  
qwen2     True        2.588414  2.460632  2.530736

In [5]:
dfs["mg"].pivot(index=["model", "is_decoder"], columns="seg_len", values="best_f1").sort_values(
    16, ascending=False
)

seg_len                    4         16        64        256
model     is_decoder                                        
llamamoe2 True        0.831850  0.781586  0.764461  0.754810
yuan      True        0.711998  0.634819  0.611333  0.598330
powermoe  True        0.673095  0.551720  0.505882  0.485872
qwen3     True        0.672163  0.541430  0.478911  0.438075
phi       True        0.651531  0.519771  0.466027  0.437805
olmoe     True        0.646949  0.509072  0.455343  0.426438
grin      True        0.637753  0.503854  0.450368  0.421200
mixtral   True        0.625494  0.493599  0.445111  0.424732
minicpm   True        0.625336  0.488538  0.437157  0.417272
jetmoe    True        0.602158  0.474540  0.427762  0.410949
llamamoe  True        0.557779  0.452880  0.416099  0.406180
xverse    True        0.536069  0.385817  0.311247  0.274691
jamba     True        0.530930  0.380786  0.311767  0.279440
deepseek2 True        0.532088  0.379159  0.306759  0.269236
deepseek  True        0.522833  0.369363  0.295573  0.257484
qwen2     True        0.502406  0.367437  0.303384  0.275186
nllb      True        0.456684  0.313525  0.261670  0.219095
qwen      True        0.472319  0.307060  0.225031  0.187072
openmoe   True        0.455252  0.287725  0.217618  0.187988
nllb      False       0.444048  0.252397  0.195115  0.165326
switch    False       0.416367  0.193265  0.123377  0.099904
          True        0.418338  0.192715  0.117753       NaN

In [6]:
dfs["mg"].pivot(
    index=["model", "is_decoder"], columns="seg_len", values=["ci_lb", "ci_ub"]
).swaplevel(0, 1, axis=1).sort_index(axis=1).sort_values((16, "ci_lb"), ascending=False)

seg_len                    4                   16                  64   \
                         ci_lb     ci_ub     ci_lb     ci_ub     ci_lb   
model     is_decoder                                                     
llamamoe2 True        0.831584  0.832086  0.781215  0.781927  0.764056   
yuan      True        0.711763  0.712224  0.634489  0.635146  0.610977   
powermoe  True        0.672926  0.673263  0.551487  0.551961  0.505597   
qwen3     True        0.671854  0.672453  0.540983  0.541858  0.478366   
phi       True        0.651136  0.651935  0.519196  0.520402  0.465376   
olmoe     True        0.646629  0.647290  0.508583  0.509616  0.454758   
grin      True        0.637370  0.638107  0.503271  0.504423  0.449715   
mixtral   True        0.625377  0.625612  0.493493  0.493707  0.444976   
minicpm   True        0.625198  0.625470  0.488427  0.488650  0.437062   
jetmoe    True        0.602040  0.602271  0.474448  0.474627  0.427677   
llamamoe  True        0.557638  0.557925  0.452812  0.452950  0.416037   
xverse    True        0.535796  0.536352  0.385522  0.386119  0.310993   
jamba     True        0.530729  0.531128  0.380567  0.381004  0.311577   
deepseek2 True        0.531857  0.532318  0.378875  0.379430  0.306523   
deepseek  True        0.522598  0.523082  0.369174  0.369558  0.295329   
qwen2     True        0.502261  0.502550  0.367379  0.367488  0.303329   
nllb      True        0.456530  0.456835  0.313143  0.313910  0.261258   
qwen      True        0.472227  0.472407  0.306880  0.307233  0.224820   
openmoe   True        0.455090  0.455408  0.287330  0.288127  0.217284   
nllb      False       0.443950  0.444142  0.252039  0.252750  0.194761   
switch    False       0.416279  0.416450  0.193005  0.193508  0.123116   
          True        0.418248  0.418426  0.192417  0.193014  0.117461   

seg_len                              256            
                         ci_ub     ci_lb     ci_ub  
model     is_decoder                                
llamamoe2 True        0.764843  0.754360  0.755251  
yuan      True        0.611700  0.597908  0.598744  
powermoe  True        0.506190  0.485549  0.486205  
qwen3     True        0.479414  0.437414  0.438741  
phi       True        0.466704  0.437034  0.438603  
olmoe     True        0.455937  0.425742  0.427139  
grin      True        0.451004  0.420436  0.421933  
mixtral   True        0.445228  0.424597  0.424857  
minicpm   True        0.437256  0.417183  0.417355  
jetmoe    True        0.427847  0.410866  0.411022  
llamamoe  True        0.416163  0.406132  0.406230  
xverse    True        0.311507  0.274414  0.274966  
jamba     True        0.311965  0.279195  0.279686  
deepseek2 True        0.307003  0.268942  0.269534  
deepseek  True        0.295831  0.257228  0.257759  
qwen2     True        0.303440  0.275120  0.275255  
nllb      True        0.262107  0.218652  0.219534  
qwen      True        0.225225  0.186869  0.187274  
openmoe   True        0.217956  0.187538  0.188410  
nllb      False       0.195449  0.164954  0.165690  
switch    False       0.123631  0.099562  0.100240  
          True        0.118047       NaN       NaN

In [7]:
dfs["mg"].assign(
    ci_dist=np.maximum(
        dfs["mg"]["ci_ub"] - dfs["mg"]["best_f1"], dfs["mg"]["best_f1"] - dfs["mg"]["ci_lb"]
    )
).pivot(index=["model", "is_decoder"], columns="seg_len", values="ci_dist")

seg_len                    4         16        64        256
model     is_decoder                                        
powermoe  True        0.000169  0.000241  0.000308  0.000333
llamamoe  True        0.000146  0.000070  0.000064  0.000050
olmoe     True        0.000341  0.000544  0.000593  0.000701
switch    False       0.000088  0.000260  0.000262  0.000341
          True        0.000090  0.000299  0.000294       NaN
llamamoe2 True        0.000265  0.000371  0.000406  0.000450
jetmoe    True        0.000118  0.000092  0.000085  0.000082
openmoe   True        0.000162  0.000403  0.000338  0.000450
minicpm   True        0.000138  0.000112  0.000099  0.000089
qwen      True        0.000092  0.000180  0.000211  0.000203
deepseek2 True        0.000231  0.000284  0.000245  0.000298
deepseek  True        0.000249  0.000195  0.000258  0.000275
xverse    True        0.000283  0.000302  0.000259  0.000277
qwen3     True        0.000309  0.000447  0.000546  0.000665
yuan      True        0.000236  0.000330  0.000367  0.000423
phi       True        0.000404  0.000631  0.000677  0.000798
grin      True        0.000383  0.000583  0.000652  0.000764
mixtral   True        0.000118  0.000108  0.000135  0.000135
jamba     True        0.000202  0.000219  0.000198  0.000246
nllb      False       0.000098  0.000359  0.000354  0.000372
          True        0.000153  0.000385  0.000436  0.000443
qwen2     True        0.000145  0.000058  0.000056  0.000070

In [8]:
mldf = pd.merge(
    dfs["mg"],
    pd.read_parquet("./output/loss.parquet")
    .groupby("model", as_index=False, observed=True)[["loss"]]
    .mean(),
)

mldf

model  is_decoder  seg_len     act_r   best_f1     ci_lb     ci_ub  \
0   powermoe        True        4  0.200000  0.673095  0.672926  0.673263   
1   powermoe        True       16  0.200000  0.551720  0.551487  0.551961   
2   powermoe        True       64  0.200000  0.505882  0.505597  0.506190   
3   powermoe        True      256  0.200000  0.485872  0.485549  0.486205   
4   llamamoe        True        4  0.250000  0.557779  0.557638  0.557925   
..       ...         ...      ...       ...       ...       ...       ...   
82      nllb        True      256  0.015625  0.219095  0.218652  0.219534   
83     qwen2        True        4  0.125000  0.502406  0.502261  0.502550   
84     qwen2        True       16  0.125000  0.367437  0.367379  0.367488   
85     qwen2        True       64  0.125000  0.303384  0.303329  0.303440   
86     qwen2        True      256  0.125000  0.275186  0.275120  0.275255   

      best_m         model_name model_abbr model_type  model_num_params  \
0   1.103515        PowerMoE-3B         PW     causal              3.30   
1   1.392749        PowerMoE-3B         PW     causal              3.30   
2   1.488992        PowerMoE-3B         PW     causal              3.30   
3   1.579756        PowerMoE-3B         PW     causal              3.30   
4   1.029198  LLaMA-MoE-v1-3.5B        LL1     causal              6.74   
..       ...                ...        ...        ...               ...   
82  1.454345       NLLB-MoE-54B         NL    seq2seq             54.50   
83  0.818744     Qwen2-57B-A14B        QW2     causal             57.41   
84  2.588414     Qwen2-57B-A14B        QW2     causal             57.41   
85  2.460632     Qwen2-57B-A14B        QW2     causal             57.41   
86  2.530736     Qwen2-57B-A14B        QW2     causal             57.41   

    model_num_layers  model_num_experts  model_top_k         model_attn  \
0                 32                 40            8  flash_attention_2   
1                 32                 40            8  flash_attention_2   
2                 32                 40            8  flash_attention_2   
3                 32                 40            8  flash_attention_2   
4                 32                 16            4              eager   
..               ...                ...          ...                ...   
82                48                128            2              eager   
83                28                 64            8  flash_attention_2   
84                28                 64            8  flash_attention_2   
85                28                 64            8  flash_attention_2   
86                28                 64            8  flash_attention_2   

        loss  
0   1.675532  
1   1.675532  
2   1.675532  
3   1.675532  
4   1.779338  
..       ...  
82  2.530380  
83  1.616623  
84  1.616623  
85  1.616623  
86  1.616623  

[87 rows x 17 columns]

In [9]:
fig = make_subplots(rows=1, cols=len(seg_lens), shared_xaxes="all", horizontal_spacing=0.01)

text_pos = [
    {
        "powermoe": "middle right",
        "llamamoe": "top center",
        "olmoe": "middle right",
        "switch": ["middle left", "middle right"],
        "llamamoe2": "bottom center",
        "jetmoe": "top center",
        "openmoe": "middle right",
        "minicpm": "middle right",
        "qwen": "bottom center",
        "deepseek2": "middle right",
        "deepseek": "middle left",
        "xverse": "bottom right",
        "qwen3": "middle right",
        "yuan": "bottom center",
        "phi": "bottom center",
        "grin": "middle left",
        "mixtral": "top center",
        "jamba": "top center",
        "nllb": ["middle left", "middle left"],
        "qwen2": "bottom center",
    },
    {
        "powermoe": "top center",
        "llamamoe": "middle left",
        "olmoe": "bottom center",
        "switch": ["bottom center", "top center"],
        "llamamoe2": "bottom center",
        "jetmoe": "middle left",
        "openmoe": "middle left",
        "minicpm": "bottom center",
        "qwen": "bottom center",
        "deepseek2": "middle right",
        "deepseek": "bottom center",
        "xverse": "bottom center",
        "qwen3": "bottom center",
        "yuan": "bottom center",
        "phi": "top center",
        "grin": "middle left",
        "mixtral": "middle right",
        "jamba": "top center",
        "nllb": ["bottom center", "bottom center"],
        "qwen2": "middle left",
    },
    {
        "powermoe": "top center",
        "llamamoe": "middle left",
        "olmoe": "bottom center",
        "switch": ["middle right", "middle left"],
        "llamamoe2": "bottom center",
        "jetmoe": "middle left",
        "openmoe": "bottom center",
        "minicpm": "middle right",
        "qwen": "middle left",
        "deepseek2": "middle right",
        "deepseek": "middle left",
        "xverse": "bottom center",
        "qwen3": "bottom center",
        "yuan": "bottom center",
        "phi": "middle right",
        "grin": "middle left",
        "mixtral": "middle right",
        "jamba": "top center",
        "nllb": ["bottom center", "bottom center"],
        "qwen2": "bottom center",
    },
    {
        "powermoe": "top center",
        "llamamoe": "middle left",
        "olmoe": "middle left",
        "switch": ["bottom center", "bottom center"],
        "llamamoe2": "bottom center",
        "jetmoe": "middle left",
        "openmoe": "bottom center",
        "minicpm": "middle left",
        "qwen": "bottom center",
        "deepseek2": "middle right",
        "deepseek": "middle right",
        "xverse": "bottom center",
        "qwen3": "bottom center",
        "yuan": "bottom center",
        "phi": "middle right",
        "grin": "middle left",
        "mixtral": "middle right",
        "jamba": "top center",
        "nllb": ["bottom center", "bottom center"],
        "qwen2": "middle right",
    },
]

font_size = [16, 20, 24, 28]
show_legend = True

for i, seg_len in enumerate(seg_lens):
    col = i + 1

    for j, key in enumerate(main_model_config.index.values):
        tmpdf = mldf.query(f"model == '{key}' and seg_len == {seg_len}")

        fig.add_scatter(
            x=tmpdf["best_f1"],
            y=tmpdf["best_m"],
            hoverinfo="skip",
            marker=go.scatter.Marker(
                color=model_colors[key],
                line=go.scatter.marker.Line(color="white", width=1),
                opacity=0.7,
                size=main_model_config.loc[key, "model_num_params"] ** 0.5 * 4,
            ),
            legendgroup=key,
            mode="markers+text",
            name=new_name[key],
            showlegend=show_legend,
            text=tmpdf.apply(make_abbr, axis=1),
            textfont=go.scatter.Textfont(size=font_size[0], shadow="auto"),
            textposition=text_pos[i][key],
            zorder=100 - j,
            row=1,
            col=col,
        )

        fig.update_xaxes(
            tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), text=f"SRP(E,{seg_len})"
            ),
            row=1,
            col=col,
        )

        fig.update_yaxes(range=[0.5, 4], showticklabels=col == 1, row=1, col=col)

        if col == 1:
            fig.update_yaxes(
                tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
                title=go.layout.yaxis.Title(
                    font=go.layout.yaxis.title.Font(size=font_size[2]), text="ρ(E,m)"
                ),
                row=1,
                col=col,
            )

    show_legend = False

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))

fig.update_layout(
    legend=go.layout.Legend(
        font=go.layout.legend.Font(size=font_size[1]),
        itemsizing="constant",
        orientation="h",
        y=-0.15,
        yanchor="top",
    ),
    margin=go.layout.Margin(l=60, r=30, t=15, b=15),
    width=2000,
    height=600,
)

fig.write_image("./plot/msrp.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()

In [10]:
fig = make_subplots(rows=1, cols=len(seg_lens), shared_xaxes="all", horizontal_spacing=0.01)

text_pos = [
    {
        "powermoe": "middle right",
        "llamamoe": "middle right",
        "olmoe": "bottom center",
        "llamamoe2": "bottom center",
        "jetmoe": "middle left",
        "openmoe": "bottom center",
        "minicpm": "top center",
        "qwen": "middle left",
        "deepseek2": "bottom center",
        "deepseek": "top center",
        "xverse": "middle left",
        "qwen3": "middle right",
        "yuan": "middle right",
        "phi": "middle right",
        "grin": "middle left",
        "mixtral": "bottom center",
        "jamba": "top center",
        "qwen2": "middle left",
    },
    {
        "powermoe": "middle right",
        "llamamoe": "top center",
        "olmoe": "bottom center",
        "llamamoe2": "bottom center",
        "jetmoe": "top center",
        "openmoe": "bottom center",
        "minicpm": "top center",
        "qwen": "top center",
        "deepseek2": "middle right",
        "deepseek": "middle left",
        "xverse": "middle left",
        "qwen3": "middle right",
        "yuan": "middle right",
        "phi": "middle right",
        "grin": "middle left",
        "mixtral": "bottom center",
        "jamba": "top center",
        "qwen2": "bottom center",
    },
    {
        "powermoe": "middle right",
        "llamamoe": "middle left",
        "olmoe": "bottom center",
        "llamamoe2": "bottom center",
        "jetmoe": "middle left",
        "openmoe": "bottom center",
        "minicpm": "top center",
        "qwen": "top center",
        "deepseek2": "middle right",
        "deepseek": "middle left",
        "xverse": "middle left",
        "qwen3": "middle right",
        "yuan": "middle right",
        "phi": "middle right",
        "grin": "middle left",
        "mixtral": "bottom center",
        "jamba": "top center",
        "qwen2": "bottom center",
    },
    {
        "powermoe": "middle right",
        "llamamoe": "middle left",
        "olmoe": "bottom center",
        "llamamoe2": "bottom center",
        "jetmoe": "middle left",
        "openmoe": "bottom center",
        "minicpm": "top center",
        "qwen": "top center",
        "deepseek2": "bottom center",
        "deepseek": "middle left",
        "xverse": "middle left",
        "qwen3": "middle right",
        "yuan": "middle right",
        "phi": "middle right",
        "grin": "middle left",
        "mixtral": "bottom center",
        "jamba": "top center",
        "qwen2": "middle right",
    },
]

font_size = [16, 20, 24, 28]
show_legend = True

for i, seg_len in enumerate(seg_lens):
    col = i + 1

    for j, key in enumerate(main_model_config.query("model_type == 'causal'").index.values):
        tmpdf = mldf.query(f"model == '{key}' and seg_len == {seg_len}")

        fig.add_scatter(
            x=tmpdf["best_f1"],
            y=tmpdf["loss"],
            hoverinfo="skip",
            marker=go.scatter.Marker(
                color=model_colors[key],
                line=go.scatter.marker.Line(color="white", width=1),
                opacity=0.7,
                size=main_model_config.loc[key, "model_num_params"] ** 0.5 * 4,
            ),
            legendgroup=key,
            mode="markers+text",
            name=new_name[key],
            showlegend=show_legend,
            text=tmpdf.apply(make_abbr, axis=1),
            textfont=go.scatter.Textfont(size=font_size[0], shadow="auto"),
            textposition=text_pos[i][key],
            zorder=100 - j,
            row=1,
            col=col,
        )

        fig.update_xaxes(
            tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), text=f"SRP(E,{seg_len})"
            ),
            row=1,
            col=col,
        )

        fig.update_yaxes(range=[1, 4], showticklabels=col == 1, row=1, col=col)

        if col == 1:
            fig.update_yaxes(
                tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
                title=go.layout.yaxis.Title(
                    font=go.layout.yaxis.title.Font(size=font_size[2]), text="log PPL"
                ),
                row=1,
                col=col,
            )

    show_legend = False

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))

fig.update_layout(
    legend=go.layout.Legend(
        font=go.layout.legend.Font(size=font_size[1]),
        itemsizing="constant",
        orientation="h",
        y=-0.15,
        yanchor="top",
    ),
    margin=go.layout.Margin(l=60, r=30, t=15, b=15),
    width=2000,
    height=600,
)

fig.write_image("./plot/msrpls.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()

In [11]:
ldf = dfs["lg"]
ldf

model  is_decoder  layer_idx  seg_len  act_r   best_f1     ci_lb  \
0     powermoe        True          0        4  0.200  0.661282  0.661011   
1     powermoe        True          0       16  0.200  0.581990  0.581716   
2     powermoe        True          0       64  0.200  0.560074  0.559798   
3     powermoe        True          0      256  0.200  0.552070  0.551776   
4     powermoe        True          1        4  0.200  0.877082  0.876993   
...        ...         ...        ...      ...    ...       ...       ...   
2713     qwen2        True         26      256  0.125  0.237058  0.236984   
2714     qwen2        True         27        4  0.125  0.471690  0.471625   
2715     qwen2        True         27       16  0.125  0.328063  0.327986   
2716     qwen2        True         27       64  0.125  0.260114  0.260041   
2717     qwen2        True         27      256  0.125  0.235271  0.235208   

         ci_ub    best_m      model_name model_abbr model_type  \
0     0.661563  1.178276     PowerMoE-3B         PW     causal   
1     0.582293  1.628545     PowerMoE-3B         PW     causal   
2     0.560361  1.731949     PowerMoE-3B         PW     causal   
3     0.552368  1.744225     PowerMoE-3B         PW     causal   
4     0.877178  1.021213     PowerMoE-3B         PW     causal   
...        ...       ...             ...        ...        ...   
2713  0.237134  4.488435  Qwen2-57B-A14B        QW2     causal   
2714  0.471753  3.240069  Qwen2-57B-A14B        QW2     causal   
2715  0.328135  2.584436  Qwen2-57B-A14B        QW2     causal   
2716  0.260187  3.259918  Qwen2-57B-A14B        QW2     causal   
2717  0.235336  4.568724  Qwen2-57B-A14B        QW2     causal   

      model_num_params  model_num_layers  model_num_experts  model_top_k  \
0                 3.30                32                 40            8   
1                 3.30                32                 40            8   
2                 3.30                32                 40            8   
3                 3.30                32                 40            8   
4                 3.30                32                 40            8   
...                ...               ...                ...          ...   
2713             57.41                28                 64            8   
2714             57.41                28                 64            8   
2715             57.41                28                 64            8   
2716             57.41                28                 64            8   
2717             57.41                28                 64            8   

             model_attn  
0     flash_attention_2  
1     flash_attention_2  
2     flash_attention_2  
3     flash_attention_2  
4     flash_attention_2  
...                 ...  
2713  flash_attention_2  
2714  flash_attention_2  
2715  flash_attention_2  
2716  flash_attention_2  
2717  flash_attention_2  

[2078 rows x 17 columns]

In [12]:
num_cols = 10
num_rows = (len(main_model_config) - 1) // num_cols + 1

fig = make_subplots(
    rows=num_rows,
    cols=num_cols,
    shared_xaxes="all",
    shared_yaxes="all",
    horizontal_spacing=0.07,
    vertical_spacing=0.11,
    subplot_titles=sorted_model_keys.map(new_name).values,
    specs=[[{"secondary_y": True, "r": -0.06} for _ in range(num_cols)] for _ in range(num_rows)],
)

font_size = [16, 16, 18, 20]
show_legend = True

for i, key in enumerate(sorted_model_keys):
    if (ldf["model"] == key).sum() == 0:
        continue

    row = i // num_cols + 1
    col = i % num_cols + 1
    num_layers = model_config.loc[key, "num_layers"]

    for seg_len in seg_lens:
        tmpdf = ldf.query(f"model == '{key}' and seg_len == {seg_len}")
        if len(tmpdf) == 0:
            continue

        layer_idx = tmpdf["layer_idx"] + 1
        if model_config.loc[key, "type"] == "seq2seq":
            layer_idx += tmpdf["is_decoder"] * model_config.loc[key, "num_layers"] // 2

        f1_name = f"SRP(E,{seg_len})"
        m_name = f"ρ(E,{seg_len})"

        fig.add_scatter(
            x=layer_idx / num_layers,
            y=tmpdf["best_f1"],
            hoverinfo="skip",
            legendgroup=f1_name,
            line=go.scatter.Line(color=seg_len_colors[seg_len]),
            mode="lines",
            name=f1_name,
            showlegend=show_legend,
            row=row,
            col=col,
        )

        fig.add_scatter(
            x=layer_idx / num_layers,
            y=tmpdf["best_m"],
            customdata=layer_idx,
            hoverinfo="skip",
            legendgroup=m_name,
            line=go.scatter.Line(color=seg_len_colors[seg_len], dash="dot"),
            mode="lines",
            name=m_name,
            opacity=0.5,
            secondary_y=True,
            showlegend=show_legend,
            row=row,
            col=col,
        )

    show_legend = False

    fig.update_xaxes(
        showticklabels=True,
        tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
        tickvals=[1 / num_layers, 0.5, 1],
        ticktext=[1, num_layers // 2, num_layers],
        row=row,
        col=col,
    )

    if row == num_rows:
        fig.update_xaxes(
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), standoff=1, text="Layer"
            ),
            row=row,
            col=col,
        )

    fig.update_yaxes(showticklabels=col == 1, row=row, col=col, secondary_y=False)

    fig.update_yaxes(
        range=[0.5, 5.5], showticklabels=col == num_cols, row=row, col=col, secondary_y=True
    )

    if col == 1:
        fig.update_yaxes(
            tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
            title=go.layout.yaxis.Title(
                font=go.layout.yaxis.title.Font(size=font_size[2]), text="SRP(E,m)"
            ),
            row=row,
            col=col,
            secondary_y=False,
        )

    if col == num_cols:
        fig.update_yaxes(
            tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
            title=go.layout.yaxis.Title(
                font=go.layout.yaxis.title.Font(size=font_size[2]), text="ρ(E,m)"
            ),
            row=row,
            col=col,
            secondary_y=True,
        )

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))

fig.update_layout(
    legend=go.layout.Legend(
        font=go.layout.legend.Font(size=font_size[2]), orientation="h", x=0.47, xanchor="center"
    ),
    margin=go.layout.Margin(l=60, r=15, t=30, b=15),
    width=2000,
    height=500,
)

fig.write_image("./plot/lsrp.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()

In [13]:
sddf = pd.merge(
    dfs["mg"],
    dfs["eg"]
    .groupby(["model", "is_decoder", "seg_len"], as_index=False, observed=True)
    .aggregate(act_r_std=("act_r", "std")),
)

sddf.pivot(
    index=["model", "is_decoder"], columns="seg_len", values=["best_f1", "act_r_std"]
).sort_values(("best_f1", 16), ascending=False)

best_f1                               act_r_std  \
seg_len                    4         16        64        256       4     
model     is_decoder                                                     
llamamoe2 True        0.831850  0.781586  0.764461  0.754810  0.289824   
yuan      True        0.711998  0.634819  0.611333  0.598330  0.138641   
powermoe  True        0.673095  0.551720  0.505882  0.485872  0.129049   
qwen3     True        0.672163  0.541430  0.478911  0.438075  0.031899   
phi       True        0.651531  0.519771  0.466027  0.437805  0.048878   
olmoe     True        0.646949  0.509072  0.455343  0.426438  0.067964   
grin      True        0.637753  0.503854  0.450368  0.421200  0.038926   
mixtral   True        0.625494  0.493599  0.445111  0.424732  0.027064   
minicpm   True        0.625336  0.488538  0.437157  0.417272  0.026123   
jetmoe    True        0.602158  0.474540  0.427762  0.410949  0.011271   
llamamoe  True        0.557779  0.452880  0.416099  0.406180  0.026594   
xverse    True        0.536069  0.385817  0.311247  0.274691  0.027195   
jamba     True        0.530930  0.380786  0.311767  0.279440  0.030569   
deepseek2 True        0.532088  0.379159  0.306759  0.269236  0.023562   
deepseek  True        0.522833  0.369363  0.295573  0.257484  0.020399   
qwen2     True        0.502406  0.367437  0.303384  0.275186  0.067348   
nllb      True        0.456684  0.313525  0.261670  0.219095  0.021302   
qwen      True        0.472319  0.307060  0.225031  0.187072  0.005903   
openmoe   True        0.455252  0.287725  0.217618  0.187988  0.025732   
nllb      False       0.444048  0.252397  0.195115  0.165326  0.017424   
switch    False       0.416367  0.193265  0.123377  0.099904  0.005788   
          True        0.418338  0.192715  0.117753       NaN  0.006949   

                                                    
seg_len                    16        64        256  
model     is_decoder                                
llamamoe2 True        0.290156  0.290434  0.290639  
yuan      True        0.138634  0.138610  0.138607  
powermoe  True        0.129093  0.129119  0.129163  
qwen3     True        0.031877  0.031715  0.031542  
phi       True        0.048935  0.048964  0.048970  
olmoe     True        0.067876  0.067566  0.067115  
grin      True        0.038890  0.038726  0.038545  
mixtral   True        0.027038  0.026876  0.026741  
minicpm   True        0.025898  0.025459  0.025024  
jetmoe    True        0.011150  0.010808  0.010442  
llamamoe  True        0.026604  0.026513  0.026371  
xverse    True        0.027119  0.026785  0.026356  
jamba     True        0.030513  0.030530  0.030577  
deepseek2 True        0.023435  0.023044  0.022633  
deepseek  True        0.020285  0.019934  0.019561  
qwen2     True        0.067390  0.067465  0.067533  
nllb      True        0.021326  0.021383  0.021669  
qwen      True        0.005829  0.005654  0.005475  
openmoe   True        0.025588  0.025002  0.024308  
nllb      False       0.017462  0.017610  0.018330  
switch    False       0.005772  0.005729  0.005698  
          True        0.006636  0.007026       NaN

In [14]:
fig = make_subplots(rows=1, cols=len(seg_lens), shared_xaxes="all", horizontal_spacing=0.01)

text_pos = [
    {
        "powermoe": "top center",
        "llamamoe": "top center",
        "olmoe": "top center",
        "switch": ["top center", "top center"],
        "llamamoe2": "top center",
        "jetmoe": "top center",
        "openmoe": "top center",
        "minicpm": "top center",
        "qwen": "top center",
        "deepseek2": "top center",
        "deepseek": "top center",
        "xverse": "top center",
        "qwen3": "top center",
        "yuan": "top center",
        "phi": "top center",
        "grin": "top center",
        "mixtral": "top center",
        "jamba": "top center",
        "nllb": ["top center", "top center"],
        "qwen2": "top center",
    },
    {
        "powermoe": "top center",
        "llamamoe": "top center",
        "olmoe": "top center",
        "switch": ["top center", "top center"],
        "llamamoe2": "top center",
        "jetmoe": "top center",
        "openmoe": "top center",
        "minicpm": "top center",
        "qwen": "top center",
        "deepseek2": "top center",
        "deepseek": "top center",
        "xverse": "top center",
        "qwen3": "top center",
        "yuan": "top center",
        "phi": "top center",
        "grin": "top center",
        "mixtral": "top center",
        "jamba": "top center",
        "nllb": ["top center", "top center"],
        "qwen2": "top center",
    },
    {
        "powermoe": "top center",
        "llamamoe": "top center",
        "olmoe": "top center",
        "switch": ["top center", "top center"],
        "llamamoe2": "top center",
        "jetmoe": "top center",
        "openmoe": "top center",
        "minicpm": "top center",
        "qwen": "top center",
        "deepseek2": "top center",
        "deepseek": "top center",
        "xverse": "top center",
        "qwen3": "top center",
        "yuan": "top center",
        "phi": "top center",
        "grin": "top center",
        "mixtral": "top center",
        "jamba": "top center",
        "nllb": ["top center", "top center"],
        "qwen2": "top center",
    },
    {
        "powermoe": "top center",
        "llamamoe": "top center",
        "olmoe": "top center",
        "switch": ["top center", "top center"],
        "llamamoe2": "top center",
        "jetmoe": "top center",
        "openmoe": "top center",
        "minicpm": "top center",
        "qwen": "top center",
        "deepseek2": "top center",
        "deepseek": "top center",
        "xverse": "top center",
        "qwen3": "top center",
        "yuan": "top center",
        "phi": "top center",
        "grin": "top center",
        "mixtral": "top center",
        "jamba": "top center",
        "nllb": ["top center", "top center"],
        "qwen2": "top center",
    },
]

font_size = [16, 20, 24, 28]
show_legend = True

for i, seg_len in enumerate(seg_lens):
    col = i + 1

    for j, key in enumerate(main_model_config.index.values):
        tmpdf = sddf.query(f"model == '{key}' and seg_len == {seg_len}")

        fig.add_scatter(
            x=tmpdf["best_f1"],
            y=tmpdf["act_r_std"],
            hoverinfo="skip",
            marker=go.scatter.Marker(
                color=model_colors[key],
                line=go.scatter.marker.Line(color="white", width=1),
                opacity=0.7,
                size=main_model_config.loc[key, "model_num_params"] ** 0.5 * 4,
            ),
            legendgroup=key,
            mode="markers+text",
            name=new_name[key],
            showlegend=show_legend,
            text=tmpdf.apply(make_abbr, axis=1),
            textfont=go.scatter.Textfont(size=font_size[0], shadow="auto"),
            textposition=text_pos[i][key],
            zorder=100 - j,
            row=1,
            col=col,
        )

        fig.update_xaxes(
            tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), text=f"SRP(E,{seg_len})"
            ),
            row=1,
            col=col,
        )

        fig.update_yaxes(range=[0, 0.35], showticklabels=col == 1, row=1, col=col)

        if col == 1:
            fig.update_yaxes(
                tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
                title=go.layout.yaxis.Title(
                    font=go.layout.yaxis.title.Font(size=font_size[2]), text="Act. Freq. SD"
                ),
                row=1,
                col=col,
            )

    show_legend = False

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))

fig.update_layout(
    legend=go.layout.Legend(
        font=go.layout.legend.Font(size=font_size[1]),
        itemsizing="constant",
        orientation="h",
        y=-0.15,
        yanchor="top",
    ),
    margin=go.layout.Margin(l=60, r=30, t=15, b=15),
    width=2000,
    height=600,
)

fig.write_image("./plot/msrpsd.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()

In [15]:
sample_seg_len = 16
edf = dfs["eg"].query(f"seg_len == {sample_seg_len}").drop(columns="seg_len")
edf

model  is_decoder  layer_idx  expert_idx     act_r   best_f1  \
1       powermoe        True          0           0  0.568817  0.740981   
5       powermoe        True          0           1  0.500232  0.686511   
9       powermoe        True          0           2  0.351072  0.572114   
13      powermoe        True          0           3  0.380526  0.600333   
17      powermoe        True          0           4  0.354294  0.570837   
...          ...         ...        ...         ...       ...       ...   
110573     qwen2        True         27          59  0.124139  0.326662   
110577     qwen2        True         27          60  0.133005  0.334691   
110581     qwen2        True         27          61  0.131245  0.334319   
110585     qwen2        True         27          62  0.133081  0.324485   
110589     qwen2        True         27          63  0.130689  0.330241   

           ci_lb     ci_ub    best_m      model_name model_abbr model_type  \
1       0.740284  0.741636  1.563594     PowerMoE-3B         PW     causal   
5       0.685632  0.687438  1.669474     PowerMoE-3B         PW     causal   
9       0.571304  0.572940  1.843012     PowerMoE-3B         PW     causal   
13      0.599478  0.601122  1.901469     PowerMoE-3B         PW     causal   
17      0.570008  0.571744  1.919815     PowerMoE-3B         PW     causal   
...          ...       ...       ...             ...        ...        ...   
110573  0.326257  0.327032  2.575495  Qwen2-57B-A14B        QW2     causal   
110577  0.334344  0.335032  2.702744  Qwen2-57B-A14B        QW2     causal   
110581  0.333973  0.334675  2.684064  Qwen2-57B-A14B        QW2     causal   
110585  0.324125  0.324846  2.682198  Qwen2-57B-A14B        QW2     causal   
110589  0.329908  0.330593  2.674947  Qwen2-57B-A14B        QW2     causal   

        model_num_params  model_num_layers  model_num_experts  model_top_k  \
1                   3.30                32                 40            8   
5                   3.30                32                 40            8   
9                   3.30                32                 40            8   
13                  3.30                32                 40            8   
17                  3.30                32                 40            8   
...                  ...               ...                ...          ...   
110573             57.41                28                 64            8   
110577             57.41                28                 64            8   
110581             57.41                28                 64            8   
110585             57.41                28                 64            8   
110589             57.41                28                 64            8   

               model_attn  
1       flash_attention_2  
5       flash_attention_2  
9       flash_attention_2  
13      flash_attention_2  
17      flash_attention_2  
...                   ...  
110573  flash_attention_2  
110577  flash_attention_2  
110581  flash_attention_2  
110585  flash_attention_2  
110589  flash_attention_2  

[23648 rows x 17 columns]

In [16]:
num_cols = 10
num_rows = (len(main_model_config) - 1) // num_cols + 1

fig = make_subplots(
    rows=num_rows,
    cols=num_cols,
    shared_xaxes="all",
    shared_yaxes="all",
    horizontal_spacing=0.02,
    vertical_spacing=0.08,
    subplot_titles=sorted_model_keys.map(new_name).values,
)


def tf(x):
    return np.log(x + 1e-5) - np.log(1 - x + 1e-5)


r = np.arange(1, 10000) / 10000
rx = tf(r)
ry = 2 * r / (r + 1)
font_size = [14, 16, 18, 20]


for i, key in enumerate(sorted_model_keys):
    if (edf["model"] == key).sum() == 0:
        continue

    row = i // num_cols + 1
    col = i % num_cols + 1
    tmpdf = edf.query(f"model == '{key}'")
    num_layers = model_config.loc[key, "num_layers"]
    layer_idx = tmpdf["layer_idx"] + 1

    if model_config.loc[key, "type"] == "seq2seq":
        layer_idx += tmpdf["is_decoder"] * num_layers // 2

    fig.add_scatter(
        x=rx,
        y=ry,
        line=go.scatter.Line(color="DarkSlateGrey", dash="dot"),
        hoverinfo="skip",
        mode="lines",
        opacity=0.5,
        showlegend=False,
        row=row,
        col=col,
    )

    fig.add_vline(
        x=tf(model_config.loc[key, "top_k"] / model_config.loc[key, "num_experts"]),
        line_dash="dash",
        line_color="green",
        opacity=0.5,
        row=row,
        col=col,
    )

    fig.add_scatter(
        x=tf(tmpdf["act_r"]),
        y=tmpdf["best_f1"],
        hoverinfo="skip",
        marker=go.scatter.Marker(
            cmax=num_layers,
            cmin=1,
            color=layer_idx + 1,
            colorbar=go.scatter.marker.ColorBar(
                len=0.49,
                thickness=10,
                x=(col - 0.23) * 0.102,
                y=(num_rows - 1 - row + 1.45) * 0.54,
                tickfont=go.scatter.marker.colorbar.Tickfont(size=font_size[0]),
                tickvals=[1, num_layers // 2, num_layers],
                title=go.scatter.marker.colorbar.Title(
                    font=go.scatter.marker.colorbar.title.Font(size=font_size[1]), text="Ly."
                ),
            ),
            size=5,
        ),
        mode="markers",
        showlegend=False,
        row=row,
        col=col,
    )

    fig.update_xaxes(
        showticklabels=row == num_rows,
        tickvals=tf(np.array([0.0001, 0.01, 0.5, 0.99, 0.9999])),
        row=row,
        col=col,
    )

    if row == num_rows:
        fig.update_xaxes(
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), standoff=0, text="Act. Freq."
            ),
            tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
            ticktext=[".0001", ".01", ".5", ".99", ".9999"],
            row=row,
            col=col,
        )

    if col == 1:
        fig.update_yaxes(
            showticklabels=True,
            title=go.layout.yaxis.Title(
                font=go.layout.yaxis.title.Font(size=font_size[2]), text=f"SRP(e,{sample_seg_len})"
            ),
            tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
            row=row,
            col=col,
        )

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))
fig.update_layout(margin=go.layout.Margin(l=60, r=15, t=30, b=90), width=2000, height=500)
fig.write_image("./plot/esrp.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()